In [1]:
%load_ext autoreload
import os

os.chdir("../")

In [2]:
%autoreload
from src.iris_manager import IRISManager
from src.utils import get_date_chunks
import datetime as dt
import pandas as pd
from tqdm import tqdm
import plotly.graph_objects as go
import logging
import os
from glob import glob
from PIL import Image
import numpy as np

logger = logging.getLogger(__name__)
BMUS = [
    ("T_BLHLB-1", "N. Scotland"),
    ("E_JAMBB-1", "C. Scotland"),
    ("T_NTRVB-1", "S. Scotland"),
    ("T_OCHLB-1", "Midlands"),
    ("T_LARKB-1", "SW England"),
    ("E_FARNB-1", "S. England"),
]

In [3]:
end = dt.datetime(2025, 8, 31, tzinfo=dt.timezone.utc)
start = dt.datetime(2025, 1, 1, tzinfo=dt.timezone.utc)
client = IRISManager()

{"timestamp": "2025-08-11T18:35:21.792603+00:00", "level": "INFO", "logger": "main", "message": "IRIS Manager initialized", "module": "iris_manager", "function": "__init__", "line": 23}


In [4]:
date_ranges = get_date_chunks(start_date=start, end_date=end)

In [5]:
dfs = {}

for bmu_tuple in tqdm(BMUS):
    _dfs = []
    for start_date, end_date in tqdm(date_ranges):
        _df = client.get_physical_data(
            bmu=bmu_tuple[0],
            start_date=start_date,
            end_date=end_date,
            datasets=["PN"],
        )
        _dfs.append(_df)

    df = pd.concat(_dfs).reset_index(drop=True)

    if df.empty:
        logger.warning(f"No records found for BMU: {bmu_tuple[0]}")
        break

    df = df.drop(["dataset", "national_grid_bm_unit"], axis=1)
    df = df.sort_values("time_from", ascending=True)

    # Resample start time to 30min and average the level to account for non-HH FPNs
    # For full precision, a time weighted average should be taken here however
    # the vast majority of FPNs submitted will be HH so this does not totally break accuracy
    df = (
        df.resample(rule="30min", on="time_from")
        .agg(
            {
                "settlement_date": "first",
                "settlement_period": "first",
                "level_from": "mean",
            }
        )
        .reset_index()
    )

    counts = df["settlement_date"].value_counts()
    df = df[df["settlement_date"].map(counts) > 47].reset_index(drop=True)

    df["HH_STRING"] = df["time_from"].dt.strftime("%H:%M")
    dfs[bmu_tuple[0]] = df

GENERATION_TIME = dt.datetime.now()


  0%|          | 0/6 [00:00<?, ?it/s]

{"timestamp": "2025-08-11T18:35:22.116394+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 338 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "T_BLHLB-1", "start_date": "2025-01-01 00:00:00+00:00", "end_date": "2025-01-08 00:00:00+00:00", "duration_s": "0.31"}


{"timestamp": "2025-08-11T18:35:22.293875+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 338 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "T_BLHLB-1", "start_date": "2025-01-08 00:00:00+00:00", "end_date": "2025-01-15 00:00:00+00:00", "duration_s": "0.18"}


{"timestamp": "2025-08-11T18:35:22.367737+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 338 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "T_BLHLB-1", "start_date": "2025-01-15 00:00:00+00:00", "end_date": "2025-01-22 00:00:00+00:00", "duration_s": "0.07"}
{"timestamp": "2025-08-11T18:35:22.452959+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 352 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "T_BLHLB-1", "start_date": "2025-01-22 00:00:00+00:00", "end_date": "2025-01-29 00:00:00+00:00", "duration_s": "0.08"}


{"timestamp": "2025-08-11T18:35:22.539262+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 382 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "T_BLHLB-1", "start_date": "2025-01-29 00:00:00+00:00", "end_date": "2025-02-05 00:00:00+00:00", "duration_s": "0.08"}
{"timestamp": "2025-08-11T18:35:22.633036+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 364 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "T_BLHLB-1", "start_date": "2025-02-05 00:00:00+00:00", "end_date": "2025-02-12 00:00:00+00:00", "duration_s": "0.09"}


...

{"timestamp": "2025-08-11T18:35:41.924061+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 338 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "E_FARNB-1", "start_date": "2025-07-02 00:00:00+00:00", "end_date": "2025-07-09 00:00:00+00:00", "duration_s": "0.07"}
{"timestamp": "2025-08-11T18:35:42.019756+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 338 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "E_FARNB-1", "start_date": "2025-07-09 00:00:00+00:00", "end_date": "2025-07-16 00:00:00+00:00", "duration_s": "0.09"}


{"timestamp": "2025-08-11T18:35:42.093671+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 338 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "E_FARNB-1", "start_date": "2025-07-16 00:00:00+00:00", "end_date": "2025-07-23 00:00:00+00:00", "duration_s": "0.07"}
{"timestamp": "2025-08-11T18:35:42.167334+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 338 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "E_FARNB-1", "start_date": "2025-07-23 00:00:00+00:00", "end_date": "2025-07-30 00:00:00+00:00", "duration_s": "0.07"}


{"timestamp": "2025-08-11T18:35:42.249097+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 338 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "E_FARNB-1", "start_date": "2025-07-30 00:00:00+00:00", "end_date": "2025-08-06 00:00:00+00:00", "duration_s": "0.08"}
{"timestamp": "2025-08-11T18:35:42.315763+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 281 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "E_FARNB-1", "start_date": "2025-08-06 00:00:00+00:00", "end_date": "2025-08-13 00:00:00+00:00", "duration_s": "0.07"}


{"timestamp": "2025-08-11T18:35:42.355276+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 0 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "E_FARNB-1", "start_date": "2025-08-13 00:00:00+00:00", "end_date": "2025-08-20 00:00:00+00:00", "duration_s": "0.04"}
{"timestamp": "2025-08-11T18:35:42.378667+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 0 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "E_FARNB-1", "start_date": "2025-08-20 00:00:00+00:00", "end_date": "2025-08-27 00:00:00+00:00", "duration_s": "0.02"}
{"timestamp": "2025-08-11T18:35:42.404235+00:00", "level": "INFO", "logger": "main", "message": "API call completed, returned 0 records", "module": "iris_manager", "function": "_call_api", "line": 53, "api_method": "balancing_physical_get", "bmu": "E_FARNB-1", "star

100%|██████████| 6/6 [00:20<00:00,  3.44s/it]


In [8]:
for bmu_tuple in tqdm(BMUS):
    _df = dfs[bmu_tuple[0]]
    fig = go.Figure(
        data=go.Heatmap(
            z=_df["level_from"],
            x=_df["HH_STRING"],
            y=_df["settlement_date"],
            colorscale="RdBu_r",
            colorbar=dict(
                lenmode="fraction", len=0.5, title=dict(text="FPN (MW)", side="right")
            ),
            zmin=_df["level_from"].min().round(),
            zmax=_df["level_from"].max().round(),
            xgap=0.5,
            ygap=0.5,
        )
    )

    fig.update_layout(
        template="simple_white",
        title=dict(
            text=f"{bmu_tuple[0]} ({bmu_tuple[1]}) - Half Hourly FPN",
            x=0.5,
            subtitle=dict(
                text=f"Start: {start.strftime('%Y-%m-%d')} - End: {end.strftime('%Y-%m-%d')} | Generated at {GENERATION_TIME.strftime('%Y-%m-%d %H:%M %Z')}",
                font=dict(color="black", size=12),
            ),
        ),
        xaxis_nticks=24,
        height=2000,
        width=750,
        plot_bgcolor="black",
        yaxis=dict(
            title=dict(text="Settlement Date"),
            autorange="reversed",
            showline=True,
            showgrid=False,
            type="date",
            tickformat="%Y-%b-%d",
        ),
        xaxis=dict(
            title=dict(text="Start Time (UTC)"),
            showline=True,
            showgrid=False,
            mirror=True,
        ),
    )

    display(fig)
    fig.write_image(
        f"./notebooks/figures/{bmu_tuple[0]}_FPN_HEATMAP_{start.strftime('%Y_%m_%d')}_{end.strftime('%Y_%m_%d')}.png",
        width=750,
        height=2000,
    )
    del fig

  0%|          | 0/6 [00:00<?, ?it/s]

 17%|█▋        | 1/6 [00:00<00:01,  3.30it/s]

 33%|███▎      | 2/6 [00:00<00:01,  3.54it/s]

 50%|█████     | 3/6 [00:00<00:00,  3.60it/s]

 67%|██████▋   | 4/6 [00:01<00:00,  3.62it/s]

 83%|████████▎ | 5/6 [00:01<00:00,  3.55it/s]

100%|██████████| 6/6 [00:01<00:00,  3.52it/s]


In [9]:
# Create horizontally combined chart # https://stackoverflow.com/a/78580732

# Use this for automatic file discovery
# images_folder = "./notebooks/figures/"
# list_im = glob(os.path.join(images_folder, "*.png"))

# Use this to specifically define order
list_im = [
    "./notebooks/figures/T_BLHLB-1_FPN_HEATMAP_2025_01_01_2025_08_31.png",
    "./notebooks/figures/E_JAMBB-1_FPN_HEATMAP_2025_01_01_2025_08_31.png",
    "./notebooks/figures/T_NTRVB-1_FPN_HEATMAP_2025_01_01_2025_08_31.png",
    "./notebooks/figures/T_OCHLB-1_FPN_HEATMAP_2025_01_01_2025_08_31.png",
    "./notebooks/figures/T_LARKB-1_FPN_HEATMAP_2025_01_01_2025_08_31.png",
    "./notebooks/figures/E_FARNB-1_FPN_HEATMAP_2025_01_01_2025_08_31.png",
]

imgs = [Image.open(i) for i in list_im]

# pick the image which is the smallest, and resize the others to match it (can be arbitrary image shape here)
min_shape = sorted([(np.sum(i.size), i.size) for i in imgs])[0][1]
imgs_comb = np.hstack([i.resize(min_shape) for i in imgs])

imgs_comb = Image.fromarray(imgs_comb)
imgs_comb.save("./notebooks/MULTI_BMU_FPN_HEATMAP.png")